In [1]:
import pandas as pd
import altair as alt

from IPython.display import Markdown

_ = alt.renderers.set_embed_options(theme="ggplot2", actions=False)


In [2]:
%load_ext sql
%config SqlMagic.displaycon = False
%sql --connection_arguments '{"read_only": true}'

In [3]:
storage_provider_power_df = %sql select * from source_spacescope_storage_provider_power
storage_provider_power_df = storage_provider_power_df.DataFrame()
storage_provider_power_df = storage_provider_power_df.assign(
    raw_pib_power=lambda df: df["raw_byte_power"] / 1024**5,
    quality_adjusted_pib_power=lambda df: df["quality_adj_power"] / 1024**5,
)


In [4]:
# | output: asis

print(
    f""" 
Updated on {storage_provider_power_df['stat_date'].max()[0:10]}.
"""
)


 
Updated on 2023-07-11.



In [5]:
# filter storage_provider_power_df with the lates stat_date

latest_storage_provider_power_df = storage_provider_power_df[
    storage_provider_power_df["stat_date"]
    == storage_provider_power_df["stat_date"].max()
]

unique_miners_with_active_power = latest_storage_provider_power_df[
    latest_storage_provider_power_df["raw_pib_power"] > 0
].nunique()["miner_id"]


In [28]:
latest_storage_provider_power_df[
    latest_storage_provider_power_df["raw_pib_power"] > 0
].describe()


raw_byte_power  quality_adj_power  raw_pib_power  \
count    3.486000e+03       3.486000e+03    3486.000000   
mean     3.777892e+15       7.326864e+15       3.355442   
std      7.926307e+15       1.109362e+16       7.039975   
min      3.435974e+10       3.435974e+10       0.000031   
25%      4.553009e+14       1.092983e+15       0.404388   
50%      1.260229e+15       2.985415e+15       1.119308   
75%      3.435407e+15       9.369940e+15       3.051254   
max      1.037020e+17       1.037020e+17      92.105835   

       quality_adjusted_pib_power  
count                 3486.000000  
mean                     6.507562  
std                      9.853117  
min                      0.000031  
25%                      0.970764  
50%                      2.651581  
75%                      8.322179  
max                     92.105835

In [34]:
# Bucketed raw power

raw_power_chart = (
    alt.Chart(
        latest_storage_provider_power_df[
            latest_storage_provider_power_df["raw_pib_power"] > 0
        ]
    )
    .mark_bar()
    .encode(
        x=alt.X(
            "raw_pib_power:Q",
            bin=alt.Bin(maxbins=20),
            title="Raw power (PiB)",
            axis=alt.Axis(format=".1f"),
        ),
        y=alt.Y("count()", title="Number of miners"),
    )
    .properties(width="container", height=500)
)

raw_power_chart


alt.Chart(...)

In [33]:
# Histogram of raw power

raw_power_hist = (
    alt.Chart(
        latest_storage_provider_power_df[
            latest_storage_provider_power_df["raw_pib_power"] > 0
        ]
    )
    .mark_bar()
    .encode(
        alt.X("raw_pib_power:Q", bin=alt.Bin(maxbins=30)),
        alt.Y("count()", title="Number of miners"),
    )
    .properties(width="container", height=700)
)

raw_power_hist


alt.Chart(...)

::: {layout="[ [1,1,1]]"}

In [7]:
# | output: asis

print(
    f"""
### Active Storage Providers
{unique_miners_with_active_power}
"""
)



### Active Storage Providers
3486



In [8]:
# | output: asis

print(
    f"""
### Total Raw Power
{latest_storage_provider_power_df['raw_pib_power'].sum():.2f} PiBs
"""
)



### Total Raw Power
11697.07 PiBs



In [9]:
# | output: asis

print(
    f"""
### Total Quality Adjusted PiB Power
{latest_storage_provider_power_df['quality_adjusted_pib_power'].sum():.2f} PiBs
"""
)



### Total Quality Adjusted PiB Power
22685.36 PiBs



:::

::: {layout="[ [1,1], [1] ]"}


In [10]:
# | output: true

display(Markdown(f"### Storage Provider Raw PiB Power"))

c = (
    alt.Chart(
        storage_provider_power_df.groupby("stat_date")
        .sum()["raw_pib_power"]
        .reset_index()
    )
    .mark_area()
    .encode(
        x=alt.X("stat_date:T", title="Date"),
        y=alt.Y("raw_pib_power:Q", title="Raw PiB Power"),
        tooltip=["stat_date", "raw_pib_power"],
        color=alt.value("#55595c"),
    )
    .properties(width="container")
)

c.display()


### Storage Provider Raw PiB Power

alt.Chart(...)

In [11]:
# | output: true

display(Markdown(f"### Storage Provider Quality Adjusted PiB Power"))

c = (
    alt.Chart(
        storage_provider_power_df.groupby("stat_date")
        .sum()["quality_adjusted_pib_power"]
        .reset_index()
    )
    .mark_area()
    .encode(
        x=alt.X("stat_date:T", title="Date"),
        y=alt.Y("quality_adjusted_pib_power:Q", title="Quality Adjusted PiB Power"),
        tooltip=["stat_date", "quality_adjusted_pib_power"],
        color=alt.value("#55595c"),
    )
    .properties(width="container")
)

c.display()


### Storage Provider Quality Adjusted PiB Power

alt.Chart(...)

In [12]:
# | output: true

display(Markdown(f"### Storage Providers With Power over Time"))

c = (
    alt.Chart(
        storage_provider_power_df[storage_provider_power_df["raw_byte_power"] > 0]
        .groupby("stat_date")
        .agg({"miner_id": "nunique"})
        .reset_index()
        .rename(columns={"stat_date": "date", "miner_id": "unique_miners"})
    )
    .mark_area()
    .encode(
        x=alt.X("date:T", title="Date"),
        y=alt.Y("unique_miners:Q", title="Unique Miners"),
        tooltip=["date", "unique_miners"],
        color=alt.value("#55595c"),
    )
    .properties(width="container")
)

c.display()


### Storage Providers With Power over Time

alt.Chart(...)

:::

::: {layout="[ [1,1], [1] ]"}

In [13]:
# | output: true

display(
    Markdown(f"### Storage Provider Raw PiB Power Growth Rate (7 Days Rolling Mean)")
)

daily_pib_power = (
    storage_provider_power_df.groupby("stat_date").sum()["raw_pib_power"].reset_index()
)

daily_pib_power = daily_pib_power.assign(
    growth_rate=lambda df: df["raw_pib_power"].pct_change(periods=7).rolling(7).mean()
    * 100
)

c = (
    alt.Chart(daily_pib_power)
    .mark_line()
    .encode(
        x=alt.X("stat_date:T", title="Date"),
        y=alt.Y("growth_rate:Q", title="Raw PiB Power Growth Rate"),
        tooltip=["stat_date", "growth_rate"],
        color=alt.value("#55595c"),
    )
    .properties(width="container")
)

line = (
    alt.Chart(pd.DataFrame({"y": [0]}))
    .mark_rule()
    .encode(y="y", color=alt.value("#999"))
)

(c + line).display()


### Storage Provider Raw PiB Power Growth Rate (7 Days Rolling Mean)

alt.LayerChart(...)

In [14]:
# | output: true

display(
    Markdown(
        f"### Storage Providers With Power over Time Growth Rate (7 Days Rolling Mean)"
    )
)

daily_miners_with_power = (
    storage_provider_power_df[storage_provider_power_df["raw_byte_power"] > 0]
    .groupby("stat_date")
    .agg({"miner_id": "nunique"})
    .reset_index()
    .rename(columns={"stat_date": "date", "miner_id": "unique_miners"})
)

daily_miners_with_power = daily_miners_with_power.assign(
    growth_rate=lambda df: df["unique_miners"].pct_change(periods=7).rolling(7).mean()
    * 100
)

c = (
    alt.Chart(daily_miners_with_power)
    .mark_bar()
    .encode(
        x=alt.X("date:T", title="Date"),
        y=alt.Y("growth_rate:Q", title="Unique Miners Growth Rate"),
        tooltip=["date", "growth_rate"],
        # Color red if negative, green if positive
        color=alt.condition(
            alt.datum.growth_rate > 0,
            alt.value("#28a745"),  # The positive color
            alt.value("#dc3545"),  # The negative color
        ),
    )
    .properties(width="container")
    # Display line at x axis 0
).interactive(bind_y=False)

line = (
    alt.Chart(pd.DataFrame({"y": [0]}))
    .mark_rule()
    .encode(y="y", color=alt.value("#999"))
)

(c + line).display()


### Storage Providers With Power over Time Growth Rate (7 Days Rolling Mean)

alt.LayerChart(...)

In [15]:
%%sql filecoin_storage_providers_locations <<

select * from filecoin_storage_providers_locations

In [16]:
filecoin_storage_providers_locations = filecoin_storage_providers_locations.DataFrame()
filecoin_storage_providers_locations.head()


provider_id         city country      region   latitude    longitude  \
0   f01959735  Los Angeles      US  California   34.05286  -118.243568   
1    f0867300        Osaka      JP       Osaka   34.69389    135.50222   
2   f02144602       Taipei      TW      Taipei  25.038328   121.564362   
3   f01992630       Dallas      US       Texas  32.962769   -96.744873   
4   f02041085        Osaka      JP       Osaka   34.69389    135.50222   

   ping_latency              updated_at  
0         6.939 2023-07-13 13:11:38.614  
1         3.846 2023-07-13 13:11:38.614  
2        16.565 2023-07-13 13:11:38.614  
3         1.002 2023-07-13 13:11:38.614  
4         0.000 2023-07-13 13:11:38.614

In [23]:
# | output: true
# Map of active miners

map_url = "https://raw.githubusercontent.com/deldersveld/topojson/master/world-continents.json"
source = alt.topo_feature(map_url, "continent")

alt.data_transformers.disable_max_rows()

base = (
    alt.Chart(source)
    .mark_geoshape(fill="lightgray", stroke="white")
    .project("mercator")
    .properties(width="container", height=800, title="Storage Providers Locations")
    .interactive()
)

i = (
    alt.Chart(filecoin_storage_providers_locations)
    .mark_circle()
    .encode(
        longitude="longitude:Q",
        latitude="latitude:Q",
        size=alt.Size("ping_latency:Q", scale=alt.Scale(range=[10, 100])),
        tooltip=["provider_id", "city", "ping_latency"],
    )
    .interactive()
)

alt.layer(base, i)


alt.LayerChart(...)

:::